<a href="https://colab.research.google.com/github/Psarf/Projects/blob/main/Olist.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Home Assignment - Data Optimization Analyst @ M:AD Growth - Paul Sarfati

Olist connects small businesses from all over Brazil to channels without hassle and with a single contract. Those merchants are able to sell their products through the Olist Store and ship them directly to the customers using Olist logistics partners.

We are asked to research this data and analyze it using SQL/Excel/Python or any other tool.

I chose to use python and SQL (with SQLite for python) 

**The plots are interactive**

I used google colab to run this notebook

# Settings

In [ ]:
import pandas as pd
import numpy as np
import os 
import plotly.express as px
pd.set_option('display.max_columns', 500)

import sqlite3
from sqlalchemy import create_engine
sql_engine = create_engine('sqlite://', echo = False)

In [ ]:
# google colab settings
from google.colab import drive
drive.mount('/content/drive')

%cd 
%cd /content/drive/MyDrive/mad

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
/root
/content/drive/MyDrive/mad


In [ ]:
#Defining a function that process a quick eda that we want to use on each table
def quick_eda(data,table_name,column_to_check_nas):
  print(f'### {table_name} shape ### \n ', data.shape, '\n')
  print(f'\n ### {table_name} info ### \n')
  data.info()
  print('\n ### Checking for missing values ### \n\n', data.isna().sum(), '\n')
  print(f'\n ### Is the {column_to_check_nas} unique? ### \n', data[column_to_check_nas].is_unique)


# Preprocessing

## Importing the data

In [ ]:
customers = pd.read_csv('olist_customers_dataset.csv')
geolocalation = pd.read_csv('olist_geolocation_dataset.csv')
order_items = pd.read_csv('olist_order_items_dataset.csv')
order_payments = pd.read_csv('olist_order_payments_dataset.csv')
reviews = pd.read_csv('olist_order_reviews_dataset.csv')
orders = pd.read_csv('olist_orders_dataset.csv')
sellers = pd.read_csv('olist_sellers_dataset.csv')
reviews = pd.read_csv('olist_order_reviews_dataset.csv')
orders = pd.read_csv('olist_orders_dataset.csv')
sellers = pd.read_csv('olist_sellers_dataset.csv')
products = pd.read_csv('olist_products_dataset.csv')
product_category_name_translation = pd.read_csv('product_category_name_translation.csv')

## Customer table

- 40% of the customers lives in the state of Sao Paulo and most of them in the city Sao Paulo 
- 12% lives in the state of Rio de Janeiro and half of them in the city of Rio

In [ ]:
quick_eda(customers,'customers', 'customer_id')

### customers shape ### 
  (99441, 5) 


 ### customers info ### 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99441 entries, 0 to 99440
Data columns (total 5 columns):
 #   Column                    Non-Null Count  Dtype 
---  ------                    --------------  ----- 
 0   customer_id               99441 non-null  object
 1   customer_unique_id        99441 non-null  object
 2   customer_zip_code_prefix  99441 non-null  int64 
 3   customer_city             99441 non-null  object
 4   customer_state            99441 non-null  object
dtypes: int64(1), object(4)
memory usage: 3.8+ MB

 ### Checking for missing values ### 

 customer_id                 0
customer_unique_id          0
customer_zip_code_prefix    0
customer_city               0
customer_state              0
dtype: int64 


 ### Is the customer_id unique? ### 
 True


In [ ]:
# print('customers shape: \n',customers.shape,'\n')
# print('### table info### \n')
# customers.info()

# print('\n ### checking for nas ### \n',customers.isna().sum()) # checking that we have no Na's 

# print('\n Is the customer id unique ? \n',customers.customer_id.is_unique) # checking that our primary key is unique

We can see that we have no duplicate values in our primary key, no missing values.

In [ ]:
px.sunburst(customers, path =["customer_state","customer_city"], title = 'Interactive plot of # of user by state with city breakdown')

In [ ]:
print('### Customers proportion by state')
customers.customer_state.value_counts(normalize = True)

### Customers proportion by state


SP    0.419807
RJ    0.129242
MG    0.117004
RS    0.054967
PR    0.050734
SC    0.036574
BA    0.033990
DF    0.021520
ES    0.020444
GO    0.020314
PE    0.016613
CE    0.013435
PA    0.009805
MT    0.009121
MA    0.007512
MS    0.007190
PB    0.005390
PI    0.004978
RN    0.004877
AL    0.004153
SE    0.003520
TO    0.002816
RO    0.002544
AM    0.001488
AC    0.000815
AP    0.000684
RR    0.000463
Name: customer_state, dtype: float64

## Order_items table

- 75% of the order items price are below 134.90 BRL
- Multiple items can be sent in the same order
- Average freight value is 20 BRL

In [ ]:
order_items.head(1)

order_id  order_item_id  \
0  00010242fe8c5a6d1ba2dd792cb16214              1   

                         product_id                         seller_id  \
0  4244733e06e7ecb4970a6e2683c13e61  48436dade18ac8b2bce089ec2a041202   

   shipping_limit_date  price  freight_value  
0  2017-09-19 09:45:35   58.9          13.29

In [ ]:
quick_eda(order_items,'order_items', 'order_id')

### order_items shape ### 
  (112650, 7) 


 ### order_items info ### 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 112650 entries, 0 to 112649
Data columns (total 7 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   order_id             112650 non-null  object 
 1   order_item_id        112650 non-null  int64  
 2   product_id           112650 non-null  object 
 3   seller_id            112650 non-null  object 
 4   shipping_limit_date  112650 non-null  object 
 5   price                112650 non-null  float64
 6   freight_value        112650 non-null  float64
dtypes: float64(2), int64(1), object(4)
memory usage: 6.0+ MB

 ### Checking for missing values ### 

 order_id               0
order_item_id          0
product_id             0
seller_id              0
shipping_limit_date    0
price                  0
freight_value          0
dtype: int64 


 ### Is the order_id unique? ### 
 False


Order id is not unique, why is this ? 
Because for every order we can have multiple items, and so for every order i will have the number of rows corresponding to the number of items 
i.e if i order 3 items, my order id will appear 3 times. 

In the table info we can see that shipping_limit_date is an object, we want to transform it to a time stamp str

In [ ]:
order_items['shipping_limit_date'] = pd.to_datetime(order_items['shipping_limit_date'])
order_items.info() #Checking that shipping_limit_date is now a time stamp object

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 112650 entries, 0 to 112649
Data columns (total 7 columns):
 #   Column               Non-Null Count   Dtype         
---  ------               --------------   -----         
 0   order_id             112650 non-null  object        
 1   order_item_id        112650 non-null  int64         
 2   product_id           112650 non-null  object        
 3   seller_id            112650 non-null  object        
 4   shipping_limit_date  112650 non-null  datetime64[ns]
 5   price                112650 non-null  float64       
 6   freight_value        112650 non-null  float64       
dtypes: datetime64[ns](1), float64(2), int64(1), object(3)
memory usage: 6.0+ MB


In [ ]:
order_items.describe()

order_item_id          price  freight_value
count  112650.000000  112650.000000  112650.000000
mean        1.197834     120.653739      19.990320
std         0.705124     183.633928      15.806405
min         1.000000       0.850000       0.000000
25%         1.000000      39.900000      13.080000
50%         1.000000      74.990000      16.260000
75%         1.000000     134.900000      21.150000
max        21.000000    6735.000000     409.680000

In [ ]:
px.histogram(order_items, x='price', title = 'Order item price plot')

## Order payments table

In this table we observed that we have 4446 duplicated order_id but 0 duplicated row. Meaning that some orders had multiple payments. 

- We have 5 payment types 
- Most of the payments are in credit card
- 2nd most popular payment type is Boleto (English: Ticket) and is a payment method in Brazil regulated by the Brazilian Federation of Banks.
- Payment installments are only available with credit_card. 
- Most of the multiple payment_sequential happened with vouchers. 
-  75% of the payments are below 170 BRL


In [ ]:
order_payments.head()

order_id  payment_sequential payment_type  \
0  b81ef226f3fe1789b1e8b2acac839d17                   1  credit_card   
1  a9810da82917af2d9aefd1278f1dcfa0                   1  credit_card   
2  25e8ea4e93396b6fa0d3dd708e76c1bd                   1  credit_card   
3  ba78997921bbcdc1373bb41e913ab953                   1  credit_card   
4  42fdf880ba16b47b59251dd489d4441a                   1  credit_card   

   payment_installments  payment_value  
0                     8          99.33  
1                     1          24.39  
2                     1          65.71  
3                     8         107.78  
4                     2         128.45

In [ ]:
quick_eda(order_payments,'order_payments', 'order_id')

### order_payments shape ### 
  (103886, 5) 


 ### order_payments info ### 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 103886 entries, 0 to 103885
Data columns (total 5 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   order_id              103886 non-null  object 
 1   payment_sequential    103886 non-null  int64  
 2   payment_type          103886 non-null  object 
 3   payment_installments  103886 non-null  int64  
 4   payment_value         103886 non-null  float64
dtypes: float64(1), int64(2), object(2)
memory usage: 4.0+ MB

 ### Checking for missing values ### 

 order_id                0
payment_sequential      0
payment_type            0
payment_installments    0
payment_value           0
dtype: int64 


 ### Is the order_id unique? ### 
 False


In [ ]:
# print('order_payments shape: \n',order_payments.shape,'\n')
# print('### table info### \n')
# order_payments.info()

# print('\n ### checking for nas ### \n',order_payments.isna().sum()) # checking that we have no Na's 

# print('\n Is the order id unique ? \n',order_payments.order_id.is_unique) # checking that our primary key is unique

print(' \n ### Duplicate order id ### \n',order_payments.duplicated(subset = 'order_id',keep='first').sum()) 


print(' \n ### Duplicate rows ### \n',order_payments.duplicated(keep='first').sum()) 

print('\n ### Payment types proportion ### \n\n',order_payments['payment_type'].value_counts(normalize =True))


print('\n ###Payment types when installments >1 ### \n\n',
      order_payments[order_payments['payment_installments'] > 1]['payment_type'].value_counts())

print('\n ###Payment types when payment_sequential >1 ### \n\n',
      order_payments[order_payments['payment_sequential'] > 1]['payment_type'].value_counts(normalize =True))

print('\n ### Payment sequential proportion ### \n\n',order_payments['payment_sequential'].value_counts(normalize =True)[0:10])

 
 ### Duplicate order id ### 
 4446
 
 ### Duplicate rows ### 
 0

 ### Payment types proportion ### 

 credit_card    0.739224
boleto         0.190440
voucher        0.055590
debit_card     0.014718
not_defined    0.000029
Name: payment_type, dtype: float64

 ###Payment types when installments >1 ### 

 credit_card    51338
Name: payment_type, dtype: int64

 ###Payment types when payment_sequential >1 ### 

 voucher        0.917808
credit_card    0.070482
debit_card     0.011489
boleto         0.000221
Name: payment_type, dtype: float64

 ### Payment sequential proportion ### 

 1     0.956433
2     0.029253
3     0.005593
4     0.002676
5     0.001636
6     0.001136
7     0.000789
8     0.000520
9     0.000414
10    0.000327
Name: payment_sequential, dtype: float64


In [ ]:
order_payments.describe()

payment_sequential  payment_installments  payment_value
count       103886.000000         103886.000000  103886.000000
mean             1.092679              2.853349     154.100380
std              0.706584              2.687051     217.494064
min              1.000000              0.000000       0.000000
25%              1.000000              1.000000      56.790000
50%              1.000000              1.000000     100.000000
75%              1.000000              4.000000     171.837500
max             29.000000             24.000000   13664.080000

In [ ]:
px.histogram(order_payments, x='payment_type', color = 'payment_sequential', title = 'Payment type broken up by # of payment sequential')

## Reviews table

- Many missings values in the review_comment_title & review_comment_message, most of the customers only give a review score without any message.
- We have duplicates in order-id meaning many reviews can be done on one order
-We have duplicated on review id, but no duplicate rows meaning that some review id refere to different orders.
- Most of the people give high review score (4-5)

In [ ]:
reviews.head(1)

review_id                          order_id  \
0  7bc2406110b926393aa56f80a40eba40  73fc7af87114b39712e6da79b0a377eb   

   review_score review_comment_title review_comment_message  \
0             4                  NaN                    NaN   

  review_creation_date review_answer_timestamp  
0  2018-01-18 00:00:00     2018-01-18 21:46:59

In [ ]:
quick_eda(reviews,'reviews', 'review_id')

### reviews shape ### 
  (99224, 7) 


 ### reviews info ### 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99224 entries, 0 to 99223
Data columns (total 7 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   review_id                99224 non-null  object
 1   order_id                 99224 non-null  object
 2   review_score             99224 non-null  int64 
 3   review_comment_title     11568 non-null  object
 4   review_comment_message   40977 non-null  object
 5   review_creation_date     99224 non-null  object
 6   review_answer_timestamp  99224 non-null  object
dtypes: int64(1), object(6)
memory usage: 5.3+ MB

 ### Checking for missing values ### 

 review_id                      0
order_id                       0
review_score                   0
review_comment_title       87656
review_comment_message     58247
review_creation_date           0
review_answer_timestamp        0
dtype: int64 


 ### Is the re

In [ ]:
print(' \n ### Duplicate review id ### \n',reviews.duplicated(subset = 'review_id',keep='first').sum())

print('\n ### Is the order id unique ? ### \n',reviews.order_id.is_unique) # checking that our primary key is unique

print(' \n ### Duplicate order id ### \n',reviews.duplicated(subset = 'order_id',keep='first').sum()) 

print(' \n ### Duplicate rows ### \n',reviews.duplicated(keep='first').sum()) 

print('\n ### Reviews score distribution ### \n\n',reviews['review_score'].value_counts(normalize = True))

 
 ### Duplicate review id ### 
 814

 ### Is the order id unique ? ### 
 False
 
 ### Duplicate order id ### 
 551
 
 ### Duplicate rows ### 
 0

 ### Reviews score distribution ### 

 5    0.577763
4    0.192917
1    0.115133
3    0.082430
2    0.031756
Name: review_score, dtype: float64


In [ ]:
# We can see that review_creation_date & review_answer_timestamp are object and should be time stamps
reviews['review_creation_date'] = pd.to_datetime(reviews['review_creation_date'])
reviews['review_answer_timestamp'] = pd.to_datetime(reviews['review_answer_timestamp'])

In [ ]:
px.histogram(reviews, x = 'review_score', color = 'review_score', title = 'Review score')

## Orders table

- Thursday and Friday have a smaller proportion of orders 
10% and 12% vs around 15% for all the other days. 
- 97% of the order are delivered
- We can see a clear positive trend in the orders quantity from jan 17 to nov 17 after it we observed a small decrease and then it continued it positive trend.
- Almost no data after august 18 but still have few cancelled orders until october 18

In [ ]:
orders.head(1)

order_id                       customer_id  \
0  e481f51cbdc54678b7cc49136f2d6af7  9ef432eb6251297304e76186b10a928d   

  order_status order_purchase_timestamp    order_approved_at  \
0    delivered      2017-10-02 10:56:33  2017-10-02 11:07:15   

  order_delivered_carrier_date order_delivered_customer_date  \
0          2017-10-04 19:55:00           2017-10-10 21:25:13   

  order_estimated_delivery_date  
0           2017-10-18 00:00:00

In [ ]:
quick_eda(orders,'orders','order_id')

### orders shape ### 
  (99441, 8) 


 ### orders info ### 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99441 entries, 0 to 99440
Data columns (total 8 columns):
 #   Column                         Non-Null Count  Dtype 
---  ------                         --------------  ----- 
 0   order_id                       99441 non-null  object
 1   customer_id                    99441 non-null  object
 2   order_status                   99441 non-null  object
 3   order_purchase_timestamp       99441 non-null  object
 4   order_approved_at              99281 non-null  object
 5   order_delivered_carrier_date   97658 non-null  object
 6   order_delivered_customer_date  96476 non-null  object
 7   order_estimated_delivery_date  99441 non-null  object
dtypes: object(8)
memory usage: 6.1+ MB

 ### Checking for missing values ### 

 order_id                            0
customer_id                         0
order_status                        0
order_purchase_timestamp            0
order_ap

Missing data for order_approved_at, order_delivered_customer_date and order_delivered_customer_date, we dont want to delet them while they still represent an order and we dont want to delet orders.



In [ ]:
#We need to transform all the object that are supposed to be time stamp object
orders['order_purchase_timestamp'] = pd.to_datetime(orders['order_purchase_timestamp'])
orders['order_approved_at'] = pd.to_datetime(orders['order_approved_at'])
orders['order_delivered_carrier_date'] = pd.to_datetime(orders['order_delivered_carrier_date'])
orders['order_delivered_customer_date'] = pd.to_datetime(orders['order_delivered_customer_date'])
orders['order_estimated_delivery_date'] = pd.to_datetime(orders['order_estimated_delivery_date'])

# Create 4 new columns year, month ,week ,day
orders['order_purchase_timestamp_year'] = orders['order_purchase_timestamp'].dt.year
orders['order_purchase_timestamp_month'] = orders['order_purchase_timestamp'].dt.month
orders['order_purchase_timestamp_week'] = orders['order_purchase_timestamp'].dt.week
orders['order_purchase_timestamp_weekday'] = orders['order_purchase_timestamp'].dt.weekday 



/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: FutureWarning:

Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.



In [ ]:
orders.order_status.value_counts(normalize = True) # Order status distribution

delivered      0.970203
shipped        0.011132
canceled       0.006285
unavailable    0.006124
invoiced       0.003158
processing     0.003027
created        0.000050
approved       0.000020
Name: order_status, dtype: float64

In [ ]:
px.histogram(orders, x='order_purchase_timestamp', color = 'order_status', title = 'Evolution of the orders by years', labels={
                     "order_purchase_timestamp": "Date",
                     'order_status' : 'Order Status'
                 })

In [ ]:
px.histogram(orders, x = 'order_purchase_timestamp_weekday',color="order_purchase_timestamp_year",
           facet_col="order_purchase_timestamp_year",
  facet_col_wrap=3  )


In [ ]:
orders['order_purchase_timestamp_weekday'].value_counts(normalize = True, ascending = True)

5    0.109482
6    0.120272
4    0.142014
3    0.148440
2    0.156394
1    0.160527
0    0.162870
Name: order_purchase_timestamp_weekday, dtype: float64

We can see that Thursday and Friday have a smaller proportion of orders 
10% and 12% vs around 15% for all the other days. 

## Sellers table

- Most of the sellers are in Sao Paulo 

In [ ]:
sellers.head(1)

seller_id  seller_zip_code_prefix seller_city  \
0  3442f8959a84dea7ee197c632cb2df15                   13023    campinas   

  seller_state  
0           SP

In [ ]:
quick_eda(sellers,'sellers','seller_id')

### sellers shape ### 
  (3095, 4) 


 ### sellers info ### 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3095 entries, 0 to 3094
Data columns (total 4 columns):
 #   Column                  Non-Null Count  Dtype 
---  ------                  --------------  ----- 
 0   seller_id               3095 non-null   object
 1   seller_zip_code_prefix  3095 non-null   int64 
 2   seller_city             3095 non-null   object
 3   seller_state            3095 non-null   object
dtypes: int64(1), object(3)
memory usage: 96.8+ KB

 ### Checking for missing values ### 

 seller_id                 0
seller_zip_code_prefix    0
seller_city               0
seller_state              0
dtype: int64 


 ### Is the seller_id unique? ### 
 True


In [ ]:
px.sunburst(sellers, path =["seller_state","seller_city"], title = 'Interactive chart of sellers states with breakdown by cities')

## Products table

In [ ]:
products.head(1)

product_id product_category_name  \
0  1e9e8ef04dbcff4541ed26657ea517e5            perfumaria   

   product_name_lenght  product_description_lenght  product_photos_qty  \
0                 40.0                       287.0                 1.0   

   product_weight_g  product_length_cm  product_height_cm  product_width_cm  
0             225.0               16.0               10.0              14.0

In [ ]:
quick_eda(products,'products','product_id')

### products shape ### 
  (32951, 9) 


 ### products info ### 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32951 entries, 0 to 32950
Data columns (total 9 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   product_id                  32951 non-null  object 
 1   product_category_name       32341 non-null  object 
 2   product_name_lenght         32341 non-null  float64
 3   product_description_lenght  32341 non-null  float64
 4   product_photos_qty          32341 non-null  float64
 5   product_weight_g            32949 non-null  float64
 6   product_length_cm           32949 non-null  float64
 7   product_height_cm           32949 non-null  float64
 8   product_width_cm            32949 non-null  float64
dtypes: float64(7), object(2)
memory usage: 2.3+ MB

 ### Checking for missing values ### 

 product_id                      0
product_category_name         610
product_name_lenght           610
produ

We have some missing values in product_category_name, product_name_lenght, product_photos_qty and product_description_lenght

In [ ]:
products.product_category_name.value_counts(normalize = True)

cama_mesa_banho                  0.093658
esporte_lazer                    0.088649
moveis_decoracao                 0.082156
beleza_saude                     0.075570
utilidades_domesticas            0.072199
                                   ...   
fashion_roupa_infanto_juvenil    0.000155
casa_conforto_2                  0.000155
pc_gamer                         0.000093
seguros_e_servicos               0.000062
cds_dvds_musicais                0.000031
Name: product_category_name, Length: 73, dtype: float64

In [ ]:
products.head()

product_id  product_category_name  \
0  1e9e8ef04dbcff4541ed26657ea517e5             perfumaria   
1  3aa071139cb16b67ca9e5dea641aaa2f                  artes   
2  96bd76ec8810374ed1b65e291975717f          esporte_lazer   
3  cef67bcfe19066a932b7673e239eb23d                  bebes   
4  9dc1a7de274444849c219cff195d0b71  utilidades_domesticas   

   product_name_lenght  product_description_lenght  product_photos_qty  \
0                 40.0                       287.0                 1.0   
1                 44.0                       276.0                 1.0   
2                 46.0                       250.0                 1.0   
3                 27.0                       261.0                 1.0   
4                 37.0                       402.0                 4.0   

   product_weight_g  product_length_cm  product_height_cm  product_width_cm  
0             225.0               16.0               10.0              14.0  
1            1000.0               30.0               18.0              20.0  
2             154.0               18.0                9.0              15.0  
3             371.0               26.0                4.0              26.0  
4             625.0               20.0               17.0              13.0

In [ ]:
products = products.merge(product_category_name_translation, on='product_category_name', how='inner')

In [ ]:
print('### Top 10 product category distribution ###')
products.product_category_name_english.value_counts(normalize = True)[0:10]

### Top 10 product category distribution ###


bed_bath_table           0.093696
sports_leisure           0.088685
furniture_decor          0.082189
health_beauty            0.075600
housewares               0.072228
auto                     0.058773
computers_accessories    0.050699
toys                     0.043646
watches_gifts            0.041110
telephony                0.035078
Name: product_category_name_english, dtype: float64

# Queries

Now that out data have been preprocessed we can start using sqlite to extract insights from it

In [ ]:
# Tranforming our tables to sql tables  
customers.to_sql(name = 'customers', con = sql_engine)
geolocalation.to_sql(name = 'geolocalation', con = sql_engine)
order_items.to_sql(name = 'items', con = sql_engine)
order_payments.to_sql(name = 'payments', con = sql_engine)
reviews.to_sql(name = 'reviews', con = sql_engine)
orders.to_sql(name = 'orders', con = sql_engine)
sellers.to_sql(name = 'sellers', con = sql_engine)
products.to_sql(name = 'products', con = sql_engine)

In [ ]:
query = "SELECT * FROM sqlite_master"
db = pd.read_sql_query(sql = query, con = sql_engine)
db[db['type'] == 'table']

type           name       tbl_name  rootpage  \
0   table      customers      customers         2   
2   table  geolocalation  geolocalation      2644   
4   table          items          items     17570   
6   table       payments       payments     22277   
8   table        reviews        reviews     24296   
10  table         orders         orders     28740   
12  table        sellers        sellers     34885   
14  table       products       products     34942   

                                                  sql  
0   CREATE TABLE customers (\n\t"index" BIGINT, \n...  
2   CREATE TABLE geolocalation (\n\t"index" BIGINT...  
4   CREATE TABLE items (\n\t"index" BIGINT, \n\tor...  
6   CREATE TABLE payments (\n\t"index" BIGINT, \n\...  
8   CREATE TABLE reviews (\n\t"index" BIGINT, \n\t...  
10  CREATE TABLE orders (\n\t"index" BIGINT, \n\to...  
12  CREATE TABLE sellers (\n\t"index" BIGINT, \n\t...  
14  CREATE TABLE products (\n\t"index" BIGINT, \n\...

In [ ]:
query1 = """
        SELECT p.product_category_name_english AS Category, count(DISTINCT o.order_id) as '# of order',
        ROUND(SUM(pa.payment_value),2) as revenue,
        ROUND((SUM(pa.payment_value)/ 17722471.5) * 100,2) as 'Whole Profit Percentage'
        From orders as o
        LEFT JOIN payments as pa on o.order_id = pa.order_id
        LEFT JOIN items as i on o.order_id = i.order_id
        LEFT JOIN products as p on i.product_id = p.product_id

        Where o.order_status = 'delivered'
        group by 1
        order by 3 DESC
        limit 10

        """

q1 = pd.read_sql_query(query1, sql_engine)
q1


Category  # of order     revenue  Whole Profit Percentage
0         bed_bath_table        9272  1692714.28                     9.55
1          health_beauty        8647  1620684.04                     9.14
2  computers_accessories        6530  1549372.59                     8.74
3        furniture_decor        6307  1394466.93                     7.87
4          watches_gifts        5495  1387362.45                     7.83
5         sports_leisure        7530  1349446.93                     7.61
6             housewares        5743  1069787.97                     6.04
7                   auto        3810   833745.67                     4.70
8           garden_tools        3448   810614.93                     4.57
9             cool_stuff        3559   744649.32                     4.20

In [ ]:
px.bar(q1, x= 'Category', y='revenue', color = 'Category', title = 'Top 10 Best Categories by Revenue')

In [ ]:
query2 = """
        Select p.product_category_name_english AS Category, count(distinct review_id) as '# of good reviews'
        From orders as o
        LEFT JOIN payments as pa on o.order_id = pa.order_id
        LEFT JOIN items as i on o.order_id = i.order_id
        LEFT JOIN products as p on i.product_id = p.product_id
        LEFT JOIN reviews as r on o.order_id = r.order_id 
        where review_score > 4
        AND o.order_status = 'delivered'
        group by 1 
        order by 2 desc
        """

pd.read_sql_query(query2, sql_engine)

Category  # of good reviews
0               health_beauty               5378
1              bed_bath_table               4958
2              sports_leisure               4618
3       computers_accessories               3687
4             furniture_decor               3571
..                        ...                ...
66        diapers_and_hygiene                 12
67             home_comfort_2                 12
68          cds_dvds_musicals                  9
69                 la_cuisine                  9
70  fashion_childrens_clothes                  7

[71 rows x 2 columns]

In [ ]:
query3 = """
        Select p.product_category_name_english AS Category, count(distinct review_id) as '# of reviews'
        From orders as o
        LEFT JOIN payments as pa on o.order_id = pa.order_id
        LEFT JOIN items as i on o.order_id = i.order_id
        LEFT JOIN products as p on i.product_id = p.product_id
        LEFT JOIN reviews as r on o.order_id = r.order_id 
        where o.order_status = 'delivered'
        group by 1 
        order by 2 desc
        """
pd.read_sql_query(query3, sql_engine)

Category  # of reviews
0              bed_bath_table          9191
1               health_beauty          8600
2              sports_leisure          7476
3       computers_accessories          6491
4             furniture_decor          6266
..                        ...           ...
67             home_comfort_2            23
68          cds_dvds_musicals            12
69                 la_cuisine            12
70  fashion_childrens_clothes             7
71      security_and_services             2

[72 rows x 2 columns]

In [ ]:
q2 = pd.read_sql_query(query2, sql_engine)
q3 = pd.read_sql_query(query3, sql_engine)
q2['total # of reviews'] = q3['# of reviews']
q2['Good Review Percent'] = q2['# of good reviews'] / q2['total # of reviews'] * 100

In [ ]:
print('### Top category by good reviews proportion')
top_category_review = q2[q2['total # of reviews'] > 1000].sort_values('Good Review Percent', ascending=False).head(10)
top_category_review

### Top category by good reviews proportion


Category  # of good reviews  total # of reviews  \
12                 perfumery               2009                3083   
17                  pet_shop               1072                1679   
15               electronics               1419                2251   
2             sports_leisure               4618                7476   
16  fashion_bags_accessories               1099                1812   
10                cool_stuff               2144                3540   
5                 housewares               3447                5719   
11              garden_tools               2056                3437   
6              watches_gifts               3198                5460   
13                      baby               1634                2790   

    Good Review Percent  
12            65.163801  
17            63.847528  
15            63.038649  
2             61.771001  
16            60.651214  
10            60.564972  
5             60.272775  
11            59.819610  
6             58.571429  
13            58.566308

In [ ]:
px.bar(top_category_review, x='Category', y = 'Good Review Percent', color = 'Category', title ='Top 10 Best category (review score)')

In [ ]:
query4 = """
        SELECT count(DISTINCT o.order_id) as '# of order',
        ROUND(SUM(pa.payment_value),2) as revenue,
        ROUND((SUM(pa.payment_value)/ 19776160.5) * 100,2) as 'Whole Profit Percentage', o.order_purchase_timestamp_weekday as WeekDay
        From orders as o
        LEFT JOIN payments as pa on o.order_id = pa.order_id
        LEFT JOIN items as i on o.order_id = i.order_id
        LEFT JOIN products as p on i.product_id = p.product_id

        Where o.order_status = 'delivered'
        group by WeekDay

        limit 10
        """

print('### Order proportion by WeekDay ###')
q4 = pd.read_sql_query(query4, sql_engine)
q4 

### Order proportion by WeekDay ###


# of order     revenue  Whole Profit Percentage  WeekDay
0       15701  3222464.57                    16.29        0
1       15503  3241134.22                    16.39        1
2       15076  3075201.51                    15.55        2
3       14323  2998814.95                    15.16        3
4       13685  2939607.40                    14.86        4
5       10555  2094454.99                    10.59        5
6       11635  2204482.80                    11.15        6

In [ ]:
px.bar(q4, x = 'WeekDay', y ='Whole Profit Percentage',  color_discrete_sequence=["lightblue"], title = 'Orders by weekday')

In [ ]:
query5 = """
        SELECT count( i.order_id) as '# of order', c.customer_id as Customer, c.customer_state, ROUND(SUM(pa.payment_value),2) as 'Money spent'
        From orders as o
        JOIN payments as pa on o.order_id = pa.order_id
        JOIN items as i on o.order_id = i.order_id
        JOIN products as p on i.product_id = p.product_id
        JOIN customers as c on o.customer_id = c.customer_id

        Where o.order_status = 'delivered'
        group by 2
        order by 4 desc
        limit 5
        """

print('###Top customers ###')
q5 = pd.read_sql_query(query5, sql_engine)
q5 

###Top customers ###


# of order                          Customer customer_state  Money spent
0           8  1617b1357756262bfa56ab541c47bc16             RJ    109312.64
1          20  bd5d39761aa56689a265d95d8d32b8be             GO     45256.00
2          20  be1b70680b9f9694d8c70f41fa3dc92b             SP     44048.00
3           6  05455dfa7cd02f13d132aa7a6a9729c6             MG     36489.24
4          10  1ff773612ab8934db89fd5afa8afe506             RJ     30186.00

In [ ]:
px.bar(q5, x='Customer', y='Money spent', color = 'customer_state', title = 'Money spend by best customers')

In [ ]:
query6 = """
        Select c.customer_state as 'Customer_state', ROUND(SUM(pa.payment_value),2) as revenue, ROUND((SUM(pa.payment_value)/ 19776160.44) * 100,2) as 'Whole Profit Percentage'
        From orders as o
        LEFT JOIN payments as pa on o.order_id = pa.order_id
        LEFT JOIN items as i on o.order_id = i.order_id
        LEFT JOIN products as p on i.product_id = p.product_id
        LEFT JOIN customers as c on o.customer_id = c.customer_id
        Where o.order_status = 'delivered'
        group by 1 
        order by 2 desc
        limit 5
        """
q6 = pd.read_sql_query(query6, sql_engine)
print('### Top State ###')
q6

### Top State ###


Customer_state     revenue  Whole Profit Percentage
0             SP  7403993.29                    37.44
1             RJ  2688933.90                    13.60
2             MG  2281229.16                    11.54
3             RS  1110976.47                     5.62
4             PR  1030822.39                     5.21

37% of the revenues came from SAO Paulo 

In [ ]:
query7 = """
        SELECT count(i.order_id) as '# of order', i.seller_id as seller, c.customer_state, ROUND(SUM(pa.payment_value),2) as 'Revenue'
        From orders as o
        JOIN payments as pa on o.order_id = pa.order_id
        JOIN items as i on o.order_id = i.order_id
        JOIN products as p on i.product_id = p.product_id
        JOIN customers as c on o.customer_id = c.customer_id

        Where o.order_status = 'delivered'
        group by 2
        order by 4 desc
        limit 5
        """

print('###Top Seller ###')
q7 = pd.read_sql_query(query5, sql_engine)
q7 

###Top Seller ###


# of order                          Customer customer_state  Money spent
0           8  1617b1357756262bfa56ab541c47bc16             RJ    109312.64
1          20  bd5d39761aa56689a265d95d8d32b8be             GO     45256.00
2          20  be1b70680b9f9694d8c70f41fa3dc92b             SP     44048.00
3           6  05455dfa7cd02f13d132aa7a6a9729c6             MG     36489.24
4          10  1ff773612ab8934db89fd5afa8afe506             RJ     30186.00

# Conclusion

- During my analysis I observed that most of the customers live in Sao Paulo state or in Rio de Janeiro. Those two states represent half of the customers while they represent less than 25% of Brazil population. Meaning that those areas regroup more wealthy people with the possibility to purchase on Olist. 
The marketing campaign should focus on those states.

- The analysis revealed that  Thursday and Friday have a smaller proportion of orders 10% and 12% vs. around 15% of all the other days. It could mean that Brazilian purchase less on those days, it required more research, but if it's true, the company should spend less on ads on those days. 

- Customers spending the most money are customers, which made many orders, some customers had up to 63 orders, showing that the company successfully to retain customers (maybe thanks to newsletters, promotions etc.) 


